Generation of the dataset 
----
Clément Domps
Yidi Zhu
MoSIG GVR

In [1]:
#some imports
import cv2 as cv
import numpy as np
import math
import matplotlib.pyplot as plt
import random

In [2]:
# function to parse the file and save the data corresponding to the location of the faces in the images
def display_faces(filename):
    file = open(filename,"r+")
    image_dict={}
    while True:
        image = file.readline().rstrip()
        if not image:
            break
        number = int(file.readline())
        image_dict[image]=[]
        for i in range(number):
            ellipse = [float(x) for x in file.readline().split()]
            maximum = int(max(ellipse[0], ellipse[1]))
            minimum = int(min(ellipse[0], ellipse[1]))
            angle = int(math.degrees(ellipse[2]))
            x,y = int(ellipse[3]),int(ellipse[4])
            face_ellipse =((maximum,minimum),angle,(x,y))
            image_dict[image].append(face_ellipse)
    file.close()
    return image_dict

In the next cell, we will create the positive images from the sets 1 to 8.

In [15]:
filename=["./FDDB-folds/FDDB-fold-0"+str(k)+"-ellipseList.txt" for k in range(1,9)] #list with all the file containing the metadata for our dataset
count_img = 0
positive_faces = []
for file in filename:
    annot = display_faces(file)
    for name in list(annot.keys()):
        for ellipse in annot[name]:
            image = cv.imread("./"+name+".jpg")
            x = ellipse[2][0]
            y = ellipse[2][1]
            maximum = ellipse[0][0]
            minimum = ellipse[0][1]
            top_x = int(x - minimum)
            top_y = int(y - maximum)
            if(top_x<0):
                top_x=0
            if(top_y<0):
                top_y=0
            face = image[top_y:top_y+maximum*2,top_x:top_x+minimum*2]
            cv.imwrite('./positive/'+str(count_img)+".jpg", face)
            count_img+=1


In [7]:
#function to check the intersection of a rectangle with a list of rectangles 
#true if the intersection is smaller than thresh
#false otherwise
def check_intersection(rectangle1,rectangles,thresh):
    #values in order l,t,r,b
    threshold = thresh
    area1 = (rectangle1[0]-rectangle1[2]+1)*(rectangle1[3]-rectangle1[1]+1)
    for rectangle2 in rectangles:
        area2 = (rectangle2[0]-rectangle2[2]+1)*(rectangle2[3]-rectangle2[1]+1)
        l = max(rectangle1[0],rectangle2[0])
        t = max(rectangle1[1],rectangle2[1])
        r = min(rectangle1[2],rectangle2[2])
        b = min(rectangle1[3],rectangle2[3])
        area = (l-r+1)*(b-t+1)
        if((area1+area2-area)==0 or (area/(area1+area2-area))>threshold):
            return False
    return True

In [9]:
# (long) function to create the negative images
def create_negative():
    filename=["./FDDB-folds/FDDB-fold-0"+str(k)+"-ellipseList.txt" for k in range(1,9)] #list with all the file containing the metadata for our dataset
    count_img = 0
    positive_faces = []
    for file in filename:
        annot = display_faces(file)
        for name in list(annot.keys()):
            rectangles = []
            image = cv.imread("./"+name+".jpg")
            for ellipse in annot[name]:
                x = ellipse[2][0]
                y = ellipse[2][1]
                maximum = ellipse[0][0]
                minimum = ellipse[0][1]
                top_x = int(x - minimum)
                top_y = int(y - maximum)
                if(top_x<0):
                    top_x=0
                if(top_y<0):
                    top_y=0
                rectangles.append([top_y,top_x, top_y+2*maximum,top_x+2*minimum])
            rectangles_back = []
            #for each face in an image, we try to find a negative image of the same size
            for ellipse in annot[name]:
                verification = False
                counter1=0
                while not verification and counter1 <1000:
                    #we randomly pick an x and y for the top left of the negative image
                    x_rand = random.randint(0,image.shape[1])
                    y_rand = random.randint(0,image.shape[0])
                    maximum = ellipse[0][0]
                    minimum = ellipse[0][1]
                    counter_max = 1000 #number of maximum times we will try to resample an x or a y
                    counter = 0
                    #we check that x+width and y+height are still in the boundary of the image
                    #we resample a new x or y if not in the boundary
                    while(x_rand+2*minimum>image.shape[1]) and counter < counter_max:
                        x_rand = random.randint(0,image.shape[1])
                        counter+=1
                    if counter < counter_max:
                        counter = 0
                    while(y_rand+2*maximum>image.shape[0]) and counter < counter_max:
                        y_rand = random.randint(0,image.shape[0])
                        counter+=1
                    if counter>=counter_max:
                        break
                    #we check for intersections with the positive images
                    verification = check_intersection([y_rand,x_rand,y_rand+2*maximum,x_rand+2*minimum],rectangles,0.01)
                    #we check for intersections with other negative images in order to have a dataset as diverse as possible
                    verification = verification and check_intersection([y_rand,x_rand,y_rand+2*maximum,x_rand+2*minimum],rectangles_back,0.5)
                    counter1 +=1
                    if verification:
                        counter1=0
                        #if it passes then we save it as a negative image
                        rectangles_back.append([y_rand,x_rand,y_rand+2*maximum,x_rand+2*minimum])
                if verification:
                    top_y = y_rand
                    top_x = x_rand
                    bottom_y = top_y+2*maximum
                    bottom_x = top_x+2*minimum
                    face = image[top_y:bottom_y,top_x:bottom_x]
                    print(str(count_img) + " taille image is "+str(image.shape[1])+" and "+str(image.shape[0]))
                    print(str(y_rand)+" to "+str(y_rand+2*maximum))
                    print(str(x_rand)+"to "+str(x_rand+2*minimum))
                    cv.imwrite('./negative/'+str(count_img)+".jpg", face)
                count_img+=1
create_negative()

0 taille image is 450 and 431
78 to 324
6to 176
1 taille image is 449 and 305
155 to 289
37to 125
2 taille image is 449 and 305
136 to 218
382to 436
3 taille image is 449 and 305
153 to 293
210to 296
4 taille image is 449 and 450
70 to 244
47to 165
5 taille image is 370 and 450
193 to 301
115to 185
6 taille image is 364 and 450
226 to 300
7to 65
7 taille image is 364 and 450
61 to 219
213to 311
8 taille image is 409 and 450
322 to 432
294to 360
9 taille image is 409 and 450
150 to 268
295to 367
10 taille image is 450 and 311
50 to 100
37to 75
11 taille image is 450 and 311
20 to 178
211to 295
12 taille image is 450 and 311
56 to 88
391to 413
13 taille image is 318 and 450
234 to 438
23to 151
14 taille image is 318 and 450
252 to 428
125to 227
22 taille image is 410 and 294
26 to 108
258to 314
24 taille image is 450 and 318
79 to 243
18to 126
25 taille image is 450 and 318
279 to 307
253to 273
26 taille image is 450 and 338
77 to 201
190to 274
27 taille image is 450 and 338
195 to 327
7

221 taille image is 321 and 450
25 to 133
35to 109
222 taille image is 321 and 450
197 to 287
107to 167
223 taille image is 321 and 450
218 to 344
172to 264
224 taille image is 358 and 450
231 to 441
8to 142
225 taille image is 450 and 374
144 to 374
100to 242
226 taille image is 450 and 330
3 to 139
141to 219
227 taille image is 258 and 450
214 to 356
92to 180
229 taille image is 258 and 450
346 to 446
60to 126
230 taille image is 307 and 450
315 to 439
53to 125
231 taille image is 450 and 331
13 to 301
246to 444
235 taille image is 337 and 450
235 to 255
44to 56
236 taille image is 337 and 450
222 to 244
312to 326
237 taille image is 337 and 450
132 to 152
257to 271
239 taille image is 450 and 333
127 to 287
10to 118
241 taille image is 449 and 370
118 to 292
10to 124
242 taille image is 450 and 357
57 to 163
247to 315
243 taille image is 450 and 357
12 to 72
266to 308
244 taille image is 450 and 357
283 to 343
221to 261
245 taille image is 450 and 357
302 to 342
384to 418
246 taille

409 taille image is 449 and 377
123 to 197
326to 380
410 taille image is 332 and 450
32 to 138
153to 233
412 taille image is 450 and 287
17 to 125
60to 128
413 taille image is 366 and 450
234 to 354
58to 140
414 taille image is 450 and 379
111 to 227
344to 420
415 taille image is 450 and 379
56 to 156
353to 421
416 taille image is 450 and 379
69 to 175
328to 404
417 taille image is 450 and 379
14 to 128
170to 246
418 taille image is 450 and 379
24 to 140
346to 406
420 taille image is 449 and 355
201 to 343
200to 294
421 taille image is 449 and 355
121 to 303
172to 290
424 taille image is 450 and 382
154 to 260
9to 83
425 taille image is 450 and 382
130 to 248
55to 123
426 taille image is 450 and 382
165 to 291
45to 127
427 taille image is 450 and 382
186 to 304
352to 426
428 taille image is 450 and 352
90 to 276
17to 141
433 taille image is 297 and 450
91 to 165
13to 49
434 taille image is 297 and 450
312 to 436
130to 202
435 taille image is 297 and 450
290 to 396
145to 211
436 taille 

7to 109
612 taille image is 306 and 450
246 to 420
110to 216
614 taille image is 450 and 335
1 to 123
236to 314
615 taille image is 450 and 335
35 to 135
215to 277
616 taille image is 450 and 335
141 to 239
378to 438
617 taille image is 450 and 433
159 to 245
383to 425
618 taille image is 450 and 433
69 to 167
47to 103
619 taille image is 450 and 433
339 to 417
370to 406
620 taille image is 450 and 433
252 to 334
218to 264
621 taille image is 450 and 433
343 to 433
349to 397
622 taille image is 450 and 433
344 to 422
379to 421
624 taille image is 450 and 433
173 to 269
391to 443
625 taille image is 410 and 307
42 to 146
15to 81
626 taille image is 410 and 307
97 to 193
34to 100
627 taille image is 346 and 450
228 to 386
30to 128
628 taille image is 430 and 450
105 to 229
221to 287
629 taille image is 430 and 450
59 to 143
248to 302
630 taille image is 430 and 450
131 to 207
76to 126
631 taille image is 430 and 450
87 to 163
368to 406
633 taille image is 449 and 384
107 to 207
174to 234

828 taille image is 450 and 353
174 to 290
71to 133
829 taille image is 335 and 450
232 to 448
2to 138
830 taille image is 344 and 450
60 to 208
49to 165
831 taille image is 344 and 450
123 to 241
245to 327
832 taille image is 450 and 314
160 to 256
247to 313
833 taille image is 450 and 314
104 to 196
366to 428
834 taille image is 450 and 314
88 to 178
151to 209
835 taille image is 450 and 334
52 to 146
167to 231
836 taille image is 450 and 334
182 to 274
159to 221
837 taille image is 450 and 314
164 to 308
56to 148
839 taille image is 313 and 410
332 to 402
17to 63
840 taille image is 410 and 284
38 to 232
45to 179
843 taille image is 450 and 401
96 to 252
314to 414
844 taille image is 450 and 401
215 to 381
261to 357
845 taille image is 450 and 331
135 to 227
368to 434
846 taille image is 450 and 331
7 to 139
344to 434
847 taille image is 278 and 410
231 to 365
41to 119
848 taille image is 450 and 297
45 to 171
28to 112
849 taille image is 450 and 297
122 to 226
42to 112
850 taille i

...

3224 taille image is 384 and 450
123 to 273
11to 109
3225 taille image is 384 and 450
21 to 147
30to 112
3226 taille image is 384 and 450
178 to 304
241to 329
3228 taille image is 450 and 343
69 to 289
189to 337
3229 taille image is 306 and 449
218 to 332
150to 218
3231 taille image is 450 and 348
140 to 264
325to 413
3232 taille image is 406 and 450
275 to 439
105to 217
3233 taille image is 450 and 360
255 to 357
301to 369
3234 taille image is 450 and 360
125 to 235
38to 110
3235 taille image is 307 and 450
224 to 430
20to 174
3238 taille image is 370 and 450
287 to 373
217to 275
3239 taille image is 370 and 450
79 to 215
248to 326
3240 taille image is 377 and 409
298 to 402
121to 191
3241 taille image is 377 and 409
291 to 343
173to 207
3242 taille image is 377 and 409
224 to 272
194to 228
3243 taille image is 377 and 409
178 to 224
55to 89
3244 taille image is 381 and 450
23 to 131
231to 309
3245 taille image is 381 and 450
185 to 317
21to 111
3246 taille image is 360 and 450
242 to

3418 taille image is 450 and 295
236 to 266
398to 416
3419 taille image is 450 and 295
244 to 280
392to 416
3420 taille image is 450 and 295
240 to 276
410to 436
3423 taille image is 450 and 295
244 to 282
243to 267
3424 taille image is 450 and 295
242 to 264
299to 315
3425 taille image is 342 and 450
215 to 365
197to 291
3426 taille image is 397 and 450
213 to 377
47to 171
3427 taille image is 344 and 410
212 to 400
212to 340
3429 taille image is 450 and 364
199 to 293
22to 92
3430 taille image is 450 and 364
223 to 363
5to 125
3431 taille image is 450 and 364
181 to 315
5to 107
3434 taille image is 319 and 450
226 to 332
167to 245
3435 taille image is 322 and 450
280 to 450
12to 126
3436 taille image is 410 and 324
37 to 139
184to 258
3437 taille image is 410 and 324
185 to 309
137to 217
3438 taille image is 410 and 324
172 to 286
72to 144
3439 taille image is 450 and 436
242 to 356
174to 246
3440 taille image is 450 and 436
203 to 231
186to 210
3441 taille image is 450 and 436
126 t

3615 taille image is 410 and 273
60 to 268
135to 245
3616 taille image is 359 and 450
124 to 314
178to 298
3617 taille image is 299 and 449
256 to 398
163to 257
3618 taille image is 357 and 450
199 to 303
131to 203
3619 taille image is 357 and 450
159 to 295
162to 248
3620 taille image is 450 and 333
196 to 318
283to 363
3621 taille image is 450 and 333
149 to 257
301to 375
3622 taille image is 450 and 333
244 to 306
61to 107
3625 taille image is 378 and 450
198 to 358
49to 137
3627 taille image is 450 and 370
152 to 278
3to 81
3628 taille image is 450 and 370
30 to 188
264to 366
3629 taille image is 450 and 370
126 to 292
273to 361
3630 taille image is 410 and 249
3 to 111
335to 403
3631 taille image is 362 and 450
84 to 244
38to 136
3632 taille image is 362 and 450
261 to 391
206to 286
3633 taille image is 450 and 343
203 to 341
3to 89
3635 taille image is 312 and 410
89 to 211
4to 76
3636 taille image is 312 and 410
137 to 229
199to 261
3638 taille image is 317 and 410
40 to 168
197

3838 taille image is 299 and 449
289 to 419
141to 221
3839 taille image is 297 and 450
209 to 327
45to 129
3842 taille image is 450 and 323
159 to 287
177to 257
3843 taille image is 450 and 367
91 to 241
83to 179
3844 taille image is 450 and 367
117 to 233
11to 97
3845 taille image is 409 and 450
108 to 208
321to 383
3846 taille image is 409 and 450
311 to 343
311to 333
3847 taille image is 409 and 450
278 to 316
124to 148
3848 taille image is 409 and 450
54 to 88
310to 334
3849 taille image is 409 and 450
314 to 350
318to 344
3850 taille image is 409 and 450
387 to 415
249to 271
3851 taille image is 409 and 450
368 to 396
112to 134
3852 taille image is 409 and 450
47 to 81
232to 256
3853 taille image is 409 and 450
372 to 404
312to 332
3854 taille image is 409 and 450
354 to 380
307to 327
3855 taille image is 409 and 450
412 to 442
76to 96
3856 taille image is 410 and 300
136 to 268
39to 131
3857 taille image is 322 and 450
293 to 433
142to 228
3858 taille image is 313 and 450
288 to 

129 to 229
23to 91
4038 taille image is 450 and 285
15 to 111
125to 193
4039 taille image is 450 and 295
140 to 282
207to 299
4040 taille image is 450 and 295
121 to 139
166to 176
4041 taille image is 450 and 295
126 to 144
403to 413
4042 taille image is 450 and 295
58 to 76
346to 358
4043 taille image is 450 and 295
259 to 279
228to 240
4044 taille image is 450 and 295
18 to 20
63to 65
4045 taille image is 450 and 295
100 to 150
303to 335
4046 taille image is 356 and 450
238 to 382
64to 162
4047 taille image is 286 and 450
257 to 403
15to 109
4050 taille image is 449 and 377
32 to 70
51to 79
4051 taille image is 449 and 377
295 to 337
189to 219
4052 taille image is 449 and 377
333 to 373
12to 38
4053 taille image is 449 and 377
34 to 72
408to 436
4054 taille image is 449 and 377
5 to 37
193to 217
4055 taille image is 449 and 377
313 to 345
11to 37
4056 taille image is 449 and 377
316 to 352
409to 433
4057 taille image is 449 and 377
68 to 84
21to 33
4058 taille image is 449 and 377
29